In [1]:
from IPython.display import HTML
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')


In [2]:
print('Testing DAN -> MBON via dopaminergic and NOS signalling')
print('Project A74, Daniel Bushey')

Testing DAN -> MBON via dopaminergic and NOS signalling
Project A74, Daniel Bushey


In [3]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))


In [4]:
import pandas as pd
import os
import sys
import numpy as np
import matplotlib.pyplot as plt
import matplotlib
import ccModules as cc
import ccModules2 as cc2

from IPython.html.widgets import interact
import pandas as pd
from IPython.display import IFrame
from bokeh.palettes import Spectral4
from bokeh.plotting import figure, output_file, show



/media/daniel/Windows1/Users/dnabu/Desktop/ResearchYogaWindows/DataJ/Programming/Python/Modules/tifffile.py:265: UserWarning: failed to import the optional _tifffile C extension module.
Loading of some compressed images will be very slow.
Tifffile.c can be obtained at http://www.lfd.uci.edu/~gohlke/
  "failed to import the optional _tifffile C extension module.\n"
/home/daniel/anaconda3/lib/python3.6/site-packages/IPython/html.py:14: ShimWarning: The `IPython.html` package has been deprecated since IPython 4.0. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


In [5]:
#load project  specific parameters
from A74_init20181101 import *

path1 /media/daniel/Windows1/Users/dnabu/Desktop/ResearchYogaWindows/DataJ/A/A74_Data2


In [6]:
#load data
#load pandas data frame
exceldata = pd.read_hdf(os.path.join(saveFig, 'Compiled_data.hdf5'), 'data')
#print(exceldata.shape)
exceldata = exceldata[exceldata['Grade'] == 1]
exceldata = exceldata[exceldata['Medium'] == 'RU486']
#pull out roi data and add each roi as separate row
exceldata = cc2.pullIntensityData(exceldata)
#need to indicate which stimulation period (1,2,3)
##take last number to represent stimulation period
exceldata['Stim_Period'] = np.zeros(len(exceldata), dtype=np.int)
for row, dseries in exceldata.iterrows():
    exceldata['Stim_Period'].loc[row] = int(dseries['Paths'][-1])
exceldata = exceldata[exceldata['Stim_Period'] == 1]
#exceldata['Sample Name']

/home/daniel/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:189: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


In [7]:
#add gentype
exceldata.loc[exceldata['Sample Name'].str.contains('A74-2'), 'Genotype'] = 'GCaMP6'
exceldata.loc[exceldata['Sample Name'].str.contains('A74-3'), 'Genotype'] = 'epac'
#exceldata[['Genotype', 'Sample Name', 'No.']]

In [8]:
#check parameters within data

parameters_to_compare = ['Genotype']
print('These are the different conditions tested.')
for cp in parameters_to_compare:
    print('Parameter:', cp)
    print(exceldata[cp].unique())

These are the different conditions tested.
Parameter: Genotype
['GCaMP6' 'epac']


In [9]:
#create a gamma roi that is mean for left and right gamma for each animal then add as new row to exceldata
for cg, cframe in exceldata.groupby(['Sample Name']):
    gammas = cframe[cframe['roi'].str.contains('gamma')]
    newrow = gammas.iloc[0]
    newrow['roi'] = 'gamma'
    newrow['intensity'] = np.mean(np.vstack(cframe['intensity'].values), axis=0)
    exceldata = exceldata.append(newrow)

/home/daniel/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """
/home/daniel/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [10]:
#Get counts
print('Number of animals tested.')
groups = exceldata.groupby(['Genotype', 'Medium', 'roi'])
groups['roi'].count()


Number of animals tested.


Genotype  Medium  roi       
GCaMP6    RU486   Background    1
                  gamma         1
                  gamma1-L      1
                  gamma1-R      1
epac      RU486   Background    2
                  gamma         2
                  gamma1-L      2
                  gamma1-R      2
Name: roi, dtype: int64

In [11]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.models import Range1d

In [12]:
output_notebook()

Loading BokehJS ...

In [13]:
#create a dictionary holding data
raw_data={}
parameters_to_compare = ['Genotype']
for cgroup, frame in exceldata.groupby(parameters_to_compare[:2]):
    frame = frame[frame['roi'].str.contains('gamma')]
    frame = cc2.intensityDataFrame(frame)
    if isinstance(cgroup, tuple):
        groupname = ''
        for cg in cgroup:
            groupname = groupname + ' ' + cg 
    else:
        groupname = cgroup
    raw_data[groupname] = frame.subtractBackground(exceldata)

In [14]:
volt = cc2.intensityDataFrame(exceldata).getVoltage()
timevolt = np.arange(0, len(volt))/100
plot=figure(y_range = (timevolt[0], timevolt[-1]), x_range = (0, 0.9), plot_width=600, plot_height=200)
plot=figure( plot_width=600, plot_height=200)
source = ColumnDataSource(data=dict(y=volt, x= timevolt ))
plot.line('x', 'y', source = source, line_width = 3, line_color ='red')
plot.x_range = Range1d(0, np.max(timevolt)*1.05)
plot.y_range = Range1d(0,np.max(volt)*1.05)
plot.xaxis.axis_label = 'Time (S)'
plot.yaxis.axis_label = 'Volt (V)'
#plot.line(timevolt,volt)
output_file("StimProtocol.html", title = 'Stimulation Protocol')
show(plot)

In [15]:
from bokeh.models import LinearAxis, Range1d
from bokeh.palettes import Spectral5
from bokeh.models import Legend

In [16]:
colors = [(139, 69, 19), (154, 205, 50), (0, 238, 238), (123, 104, 238), (221, 160, 221)]
colors = dict(zip(raw_data.keys(), colors))
print(colors)

{'GCaMP6': (139, 69, 19), 'epac': (154, 205, 50)}


In [17]:
raw_data.keys()

dict_keys(['GCaMP6', 'epac'])

In [18]:
#Intensity Data (subtract background plot)
timeStamp = cc2.intensityDataFrame(exceldata).getTimeStamp()
#get the min and max range for the data
data = []
for ckey in raw_data.keys():
    data.append( np.mean(np.vstack(raw_data[ckey]['intensity'].values), axis=0))
data=np.vstack(data)
data.shape
min1 = np.min(data)
max1 = np.max(data)
p = figure(plot_width=800, plot_height=400, y_range=(min1, max1), x_range = (0, len(timeStamp)), x_axis_label = 'Time (S)', y_axis_label = 'Intensity - Background')
#plot showing voltage
p.title.text = 'Click on legend entries to hide the corresponding lines'
p.extra_y_ranges = {"foo": Range1d(start=-0, end=1)}
p.add_layout(LinearAxis(y_range_name='foo', axis_label = 'Volt (V)'), 'right')
c = p.line(timevolt, volt, y_range_name = 'foo', line_color = (255,0, 0), line_alpha=0.5, line_width =2)

#plot showing mean data results
legend_it = [('Voltage', [c])]
for i, cgroup in enumerate(raw_data.keys()):
    c = p.line(x=timeStamp, y=np.mean(np.vstack(raw_data[cgroup]['intensity'].values), axis=0), line_width=2, line_color = colors[cgroup])
    legend_it.append((cgroup, [c]))
    
    
p.sizing_mode = 'scale_width'

legend = Legend(items = legend_it, location=(0, 200))
legend.click_policy="hide"
p.add_layout(legend, 'right')


    

#p.y_range.end = 400
#p.y_range.start =380
output_file("Mean-RawIntensity.html", title = 'Stimulation Protocol')
#p.patch(timevolt2, volt2, y_range_name = 'foo')
show(p)

In [19]:
def generateGroupNames(list1):
    #list1 = list that is converted to string
    for i, l in enumerate(list1):
        if not isinstance(l, str):
            list1[i] = str(l)
    groupname = list1[0]
    for cg in list1[1:]:
        groupname = groupname + ' ' + cg
    return groupname

In [20]:
# getting the DeltaF/F responses for each time point then placing in a dictionary
deltaFF_data={}
parameters_to_compare = ['Genotype']
stimPeriods, stimoffPeriods = cc2.voltage(cc2.intensityDataFrame(exceldata).getVoltage()).getVoltageStopStarts()
prestim = 5 # time in s to include before stimulation
poststim = 20 # time after first stimulation to include
cgen= 'A74-1'
    

#add intensity data to dictionary
for cstimindex, cstim in enumerate(stimPeriods):
    prestart = cstim - prestim
    stop = stimoffPeriods[cstimindex] + poststim
    cstimS = [str(cstim)]
    for cgroup, frame in exceldata.groupby(parameters_to_compare):
        frame = frame[frame['roi'].str.contains('gamma')]
        dFF = cc2.intensityDataFrame(frame).getdFF(prestart, cstim, stop, exceldata, transgene[cgen]['response'])
        cgroup2 = cstimS.copy()
        if isinstance(cgroup, tuple):
            cgroup2.extend(cgroup)
        else:
            cgroup2.append(cgroup)
        groupname2 = generateGroupNames(cgroup2)
        deltaFF_data[groupname2] = dFF.deltaFF()
        deltaFF_data[groupname2 + 'timeStamp'] = dFF.timeStamp
        

In [21]:
#default stim period
print('deltaF/F response for each sequential stimulation')
for cstimindex, cstim in enumerate(stimPeriods):
    #cstim = stimPeriods[1]
    prestart = cstim - prestim
    stop = stimoffPeriods[cstimindex] + poststim
    cstim = [str(cstim)]
    #get the min and max range for the data
    data = []
    for cgroup, frame in exceldata.groupby(parameters_to_compare):
        if isinstance(cgroup, tuple):
            cgroup = list(cgroup)
        else:
            cgroup = [cgroup] 
        cgroup2 = cstim.copy()
        cgroup2.extend(cgroup)
        groupname2 = generateGroupNames(cgroup2)
        data.append( np.nanmean(deltaFF_data[groupname2], axis=0))
    data=np.vstack(data)
    data.shape
    min1 = np.min(data)*1.05
    max1 = np.max(data)*1.05
    p = figure(plot_width=800, plot_height=400, y_range=(min1, max1), x_range = (prestart, stop), x_axis_label = 'Time (S)', y_axis_label = 'deltaF/F')
    #plot showing voltage
    p.title.text = 'Click on legend entries to hide the corresponding lines'
    p.extra_y_ranges = {"foo": Range1d(start=-0, end=1)}
    p.add_layout(LinearAxis(y_range_name='foo', axis_label = 'Volt (V)'), 'right')
    c = p.line(timevolt, volt, y_range_name = 'foo', line_color = (255,0, 0), line_alpha=0.5, line_width =2)
    legend_it = [('Voltage', [c])]
    #add keys to dictionary that are the current drawings
    for cgroup, frame in exceldata.groupby(parameters_to_compare):
        if isinstance(cgroup, tuple):
            cgroup = list(cgroup)
        else:
            cgroup = [cgroup]
        cgroupD = cgroup.copy()
        cgroupD.extend(['Draw'])
        cgroupD = generateGroupNames(cgroupD)
        cgroup2 = cstim.copy()
        cgroup2.extend(cgroup)
        groupname2 = generateGroupNames(cgroup2)
        deltaFF_data[cgroupD] = deltaFF_data[groupname2]

    #plot showing mean data results
    source = ColumnDataSource(data=deltaFF_data)
    for cgroup, frame in exceldata.groupby(parameters_to_compare):
        if isinstance(cgroup, tuple):
            cgroup = list(cgroup)
        else:
            cgroup = [cgroup]
        cgroupcolor = generateGroupNames(cgroup)
        #cgroupcolor = ' ' + cgroupcolor
        cgroup2 = cstim.copy()
        cgroup2.extend(cgroup)
        groupname2 = generateGroupNames(cgroup2)
        c = p.line(x=deltaFF_data[groupname2 + 'timeStamp'], y=np.mean(deltaFF_data[groupname2], axis=0), line_width=2, line_color = colors[cgroupcolor])
        legend_it.append((cgroupcolor, [c]))


    p.sizing_mode = 'scale_width'

    legend = Legend(items = legend_it, location=(0, 200))
    legend.click_policy="hide"
    p.add_layout(legend, 'right')




    #p.y_range.end = 400
    #p.y_range.start =380
    #output_file("Mean-RawIntensity.html", title = 'Stimulation Protocol')
    #p.patch(timevolt2, volt2, y_range_name = 'foo')
    show(p)

deltaF/F response for each sequential stimulation


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


/home/daniel/anaconda3/lib/python3.6/site-packages/bokeh/models/sources.py:110: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('149.99 GCaMP6', 3), ('149.99 GCaMP6timeStamp', 26), ('149.99 epac', 6), ('149.99 epactimeStamp', 26), ('209.99 GCaMP6', 3), ('209.99 GCaMP6timeStamp', 26), ('209.99 epac', 6), ('209.99 epactimeStamp', 26), ('269.99 GCaMP6', 3), ('269.99 GCaMP6timeStamp', 25), ('269.99 epac', 6), ('269.99 epactimeStamp', 25), ('29.99 GCaMP6', 3), ('29.99 GCaMP6timeStamp', 26), ('29.99 epac', 6), ('29.99 epactimeStamp', 26), ('329.99 GCaMP6', 3), ('329.99 GCaMP6timeStamp', 26), ('329.99 epac', 6), ('329.99 epactimeStamp', 26), ('89.99 GCaMP6', 3), ('89.99 GCaMP6timeStamp', 26), ('89.99 epac', 6), ('89.99 epactimeStamp', 26), ('GCaMP6 Draw', 3), ('epac Draw', 6)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))
